In [3]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
import pydicom

In [4]:
DATA_PATH = "..\\data CBIS-DDSM\\"
metadata_df = pd.read_csv(DATA_PATH + "metadata-full.csv")

In [5]:
metadata_df = metadata_df.drop(["Data Description URI","Series UID", "Subject ID", "Study UID", "SOP Class Name",
         "SOP Class UID", "Study Date", "Download Timestamp", "Collection", "3rd Party Analysis",
         "Study Description", "Manufacturer", "Modality"],axis=1)

In [6]:
metadata_df.head()

Series Description  Number of Images File Size  \
0  full mammogram images                 1  27.84 MB   
1  full mammogram images                 1  28.97 MB   
2        ROI mask images                 2  14.06 MB   
3        ROI mask images                 2  14.62 MB   
4  full mammogram images                 1  25.73 MB   

                                       File Location  
0  .\CBIS-DDSM\Calc-Test_P_00038_LEFT_CC\08-29-20...  
1  .\CBIS-DDSM\Calc-Test_P_00038_LEFT_MLO\08-29-2...  
2  .\CBIS-DDSM\Calc-Test_P_00038_LEFT_CC_1\08-29-...  
3  .\CBIS-DDSM\Calc-Test_P_00038_LEFT_MLO_1\08-29...  
4  .\CBIS-DDSM\Calc-Test_P_00038_RIGHT_CC\08-29-2...

In [7]:
LABELS_PATH = "../data CBIS-DDSM/Labels/"
mass_train, mass_test, calc_train, calc_test = pd.read_csv(LABELS_PATH + "mass_case_description_train_set.csv"), pd.read_csv(LABELS_PATH + "mass_case_description_test_set.csv"), pd.read_csv(LABELS_PATH + "calc_case_description_train_set.csv"),pd.read_csv(LABELS_PATH + "calc_case_description_test_set.csv")

In [26]:
mass_train[mass_train["image file path"].str.contains("01079")]

patient_id  breast_density left or right breast image view  \
742    P_01079               2                RIGHT         CC   
743    P_01079               2                RIGHT        MLO   

     abnormality id abnormality type mass shape            mass margins  \
742               1             mass  IRREGULAR  ILL_DEFINED-SPICULATED   
743               1             mass  IRREGULAR              SPICULATED   

     assessment  pathology  subtlety  \
742           4  MALIGNANT         3   
743           5  MALIGNANT         4   

                                       image file path  \
742  Mass-Training_P_01079_RIGHT_CC/1.3.6.1.4.1.959...   
743  Mass-Training_P_01079_RIGHT_MLO/1.3.6.1.4.1.95...   

                               cropped image file path  \
742  Mass-Training_P_01079_RIGHT_CC_1/1.3.6.1.4.1.9...   
743  Mass-Training_P_01079_RIGHT_MLO_1/1.3.6.1.4.1....   

                                    ROI mask file path  
742  Mass-Training_P_01079_RIGHT_CC_1/1.3.6.1.4.1.9...  
743  Mass-Training_P_01079_RIGHT_MLO_1/1.3.6.1.4.1....

In [7]:
calc_test.head()

patient_id  breast density left or right breast image view  abnormality id  \
0    P_00038               2                 LEFT         CC               1   
1    P_00038               2                 LEFT        MLO               1   
2    P_00038               2                RIGHT         CC               1   
3    P_00038               2                RIGHT         CC               2   
4    P_00038               2                RIGHT        MLO               1   

  abnormality type             calc type calc distribution  assessment  \
0    calcification  PUNCTATE-PLEOMORPHIC         CLUSTERED           4   
1    calcification  PUNCTATE-PLEOMORPHIC         CLUSTERED           4   
2    calcification              VASCULAR               NaN           2   
3    calcification              VASCULAR               NaN           2   
4    calcification              VASCULAR               NaN           2   

                 pathology  subtlety  \
0                   BENIGN         2   
1                   BENIGN         2   
2  BENIGN_WITHOUT_CALLBACK         5   
3  BENIGN_WITHOUT_CALLBACK         5   
4  BENIGN_WITHOUT_CALLBACK         5   

                                     image file path  \
0  Calc-Test_P_00038_LEFT_CC/1.3.6.1.4.1.9590.100...   
1  Calc-Test_P_00038_LEFT_MLO/1.3.6.1.4.1.9590.10...   
2  Calc-Test_P_00038_RIGHT_CC/1.3.6.1.4.1.9590.10...   
3  Calc-Test_P_00038_RIGHT_CC/1.3.6.1.4.1.9590.10...   
4  Calc-Test_P_00038_RIGHT_MLO/1.3.6.1.4.1.9590.1...   

                             cropped image file path  \
0  Calc-Test_P_00038_LEFT_CC_1/1.3.6.1.4.1.9590.1...   
1  Calc-Test_P_00038_LEFT_MLO_1/1.3.6.1.4.1.9590....   
2  Calc-Test_P_00038_RIGHT_CC_1/1.3.6.1.4.1.9590....   
3  Calc-Test_P_00038_RIGHT_CC_2/1.3.6.1.4.1.9590....   
4  Calc-Test_P_00038_RIGHT_MLO_1/1.3.6.1.4.1.9590...   

                                  ROI mask file path  
0  Calc-Test_P_00038_LEFT_CC_1/1.3.6.1.4.1.9590.1...  
1  Calc-Test_P_00038_LEFT_MLO_1/1.3.6.1.4.1.9590....  
2  Calc-Test_P_00038_RIGHT_CC_1/1.3.6.1.4.1.9590....  
3  Calc-Test_P_00038_RIGHT_CC_2/1.3.6.1.4.1.9590....  
4  Calc-Test_P_00038_RIGHT_MLO_1/1.3.6.1.4.1.9590...

In [8]:
calc_train.head()

patient_id  breast density left or right breast image view  abnormality id  \
0    P_00005               3                RIGHT         CC               1   
1    P_00005               3                RIGHT        MLO               1   
2    P_00007               4                 LEFT         CC               1   
3    P_00007               4                 LEFT        MLO               1   
4    P_00008               1                 LEFT         CC               1   

  abnormality type    calc type calc distribution  assessment  \
0    calcification    AMORPHOUS         CLUSTERED           3   
1    calcification    AMORPHOUS         CLUSTERED           3   
2    calcification  PLEOMORPHIC            LINEAR           4   
3    calcification  PLEOMORPHIC            LINEAR           4   
4    calcification          NaN          REGIONAL           2   

                 pathology  subtlety  \
0                MALIGNANT         3   
1                MALIGNANT         3   
2                   BENIGN         4   
3                   BENIGN         4   
4  BENIGN_WITHOUT_CALLBACK         3   

                                     image file path  \
0  Calc-Training_P_00005_RIGHT_CC/1.3.6.1.4.1.959...   
1  Calc-Training_P_00005_RIGHT_MLO/1.3.6.1.4.1.95...   
2  Calc-Training_P_00007_LEFT_CC/1.3.6.1.4.1.9590...   
3  Calc-Training_P_00007_LEFT_MLO/1.3.6.1.4.1.959...   
4  Calc-Training_P_00008_LEFT_CC/1.3.6.1.4.1.9590...   

                             cropped image file path  \
0  Calc-Training_P_00005_RIGHT_CC_1/1.3.6.1.4.1.9...   
1  Calc-Training_P_00005_RIGHT_MLO_1/1.3.6.1.4.1....   
2  Calc-Training_P_00007_LEFT_CC_1/1.3.6.1.4.1.95...   
3  Calc-Training_P_00007_LEFT_MLO_1/1.3.6.1.4.1.9...   
4  Calc-Training_P_00008_LEFT_CC_1/1.3.6.1.4.1.95...   

                                  ROI mask file path  
0  Calc-Training_P_00005_RIGHT_CC_1/1.3.6.1.4.1.9...  
1  Calc-Training_P_00005_RIGHT_MLO_1/1.3.6.1.4.1....  
2  Calc-Training_P_00007_LEFT_CC_1/1.3.6.1.4.1.95...  
3  Calc-Training_P_00007_LEFT_MLO_1/1.3.6.1.4.1.9...  
4  Calc-Training_P_00008_LEFT_CC_1/1.3.6.1.4.1.95...

In [9]:
mass_test.head()

patient_id  breast_density left or right breast image view  abnormality id  \
0    P_00016               4                 LEFT         CC               1   
1    P_00016               4                 LEFT        MLO               1   
2    P_00017               2                 LEFT         CC               1   
3    P_00017               2                 LEFT        MLO               1   
4    P_00032               3                RIGHT         CC               1   

  abnormality type mass shape   mass margins  assessment  pathology  subtlety  \
0             mass  IRREGULAR     SPICULATED           5  MALIGNANT         5   
1             mass  IRREGULAR     SPICULATED           5  MALIGNANT         5   
2             mass      ROUND  CIRCUMSCRIBED           4  MALIGNANT         4   
3             mass      ROUND    ILL_DEFINED           4  MALIGNANT         4   
4             mass      ROUND       OBSCURED           0     BENIGN         2   

                                     image file path  \
0  Mass-Test_P_00016_LEFT_CC/1.3.6.1.4.1.9590.100...   
1  Mass-Test_P_00016_LEFT_MLO/1.3.6.1.4.1.9590.10...   
2  Mass-Test_P_00017_LEFT_CC/1.3.6.1.4.1.9590.100...   
3  Mass-Test_P_00017_LEFT_MLO/1.3.6.1.4.1.9590.10...   
4  Mass-Test_P_00032_RIGHT_CC/1.3.6.1.4.1.9590.10...   

                             cropped image file path  \
0  Mass-Test_P_00016_LEFT_CC_1/1.3.6.1.4.1.9590.1...   
1  Mass-Test_P_00016_LEFT_MLO_1/1.3.6.1.4.1.9590....   
2  Mass-Test_P_00017_LEFT_CC_1/1.3.6.1.4.1.9590.1...   
3  Mass-Test_P_00017_LEFT_MLO_1/1.3.6.1.4.1.9590....   
4  Mass-Test_P_00032_RIGHT_CC_1/1.3.6.1.4.1.9590....   

                                  ROI mask file path  
0  Mass-Test_P_00016_LEFT_CC_1/1.3.6.1.4.1.9590.1...  
1  Mass-Test_P_00016_LEFT_MLO_1/1.3.6.1.4.1.9590....  
2  Mass-Test_P_00017_LEFT_CC_1/1.3.6.1.4.1.9590.1...  
3  Mass-Test_P_00017_LEFT_MLO_1/1.3.6.1.4.1.9590....  
4  Mass-Test_P_00032_RIGHT_CC_1/1.3.6.1.4.1.9590....

In [10]:
calc_train = calc_train.drop(["breast density","left or right breast","image view","abnormality id","calc type","calc distribution","pathology","subtlety"],axis=1)
calc_test = calc_test.drop(["breast density","left or right breast","image view","abnormality id","calc type","calc distribution","pathology","subtlety"],axis=1)

mass_train = mass_train.drop(["breast_density","left or right breast","image view","abnormality id","mass shape","mass margins","pathology","subtlety"],axis=1)
mass_test = mass_test.drop(["breast_density","left or right breast","image view","abnormality id","mass shape","mass margins","pathology","subtlety"],axis=1)

In [11]:
calc_train.head()

patient_id abnormality type  assessment  \
0    P_00005    calcification           3   
1    P_00005    calcification           3   
2    P_00007    calcification           4   
3    P_00007    calcification           4   
4    P_00008    calcification           2   

                                     image file path  \
0  Calc-Training_P_00005_RIGHT_CC/1.3.6.1.4.1.959...   
1  Calc-Training_P_00005_RIGHT_MLO/1.3.6.1.4.1.95...   
2  Calc-Training_P_00007_LEFT_CC/1.3.6.1.4.1.9590...   
3  Calc-Training_P_00007_LEFT_MLO/1.3.6.1.4.1.959...   
4  Calc-Training_P_00008_LEFT_CC/1.3.6.1.4.1.9590...   

                             cropped image file path  \
0  Calc-Training_P_00005_RIGHT_CC_1/1.3.6.1.4.1.9...   
1  Calc-Training_P_00005_RIGHT_MLO_1/1.3.6.1.4.1....   
2  Calc-Training_P_00007_LEFT_CC_1/1.3.6.1.4.1.95...   
3  Calc-Training_P_00007_LEFT_MLO_1/1.3.6.1.4.1.9...   
4  Calc-Training_P_00008_LEFT_CC_1/1.3.6.1.4.1.95...   

                                  ROI mask file path  
0  Calc-Training_P_00005_RIGHT_CC_1/1.3.6.1.4.1.9...  
1  Calc-Training_P_00005_RIGHT_MLO_1/1.3.6.1.4.1....  
2  Calc-Training_P_00007_LEFT_CC_1/1.3.6.1.4.1.95...  
3  Calc-Training_P_00007_LEFT_MLO_1/1.3.6.1.4.1.9...  
4  Calc-Training_P_00008_LEFT_CC_1/1.3.6.1.4.1.95...

In [14]:
# for df in [mass_train, mass_test, calc_train, calc_test]:
#     df["image file path"] = df["image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +"1-1.dcm",1)
#     df["cropped image file path"] = df["cropped image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +"1-1.dcm",1)
#     df["ROI mask file path"] = df["ROI mask file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +"1-2.dcm",1)
#     print(df.head(3))

for df in [mass_train, mass_test, calc_train, calc_test]:
    df["image file path"] = df["image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +"raw.dcm",1)
    df["cropped image file path"] = df["cropped image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +f"cropped{(str(x)[str(x).index('/')-1])}.dcm",1)
    df["ROI mask file path"] = df["ROI mask file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +f"roi{(str(x)[str(x).index('/')-1])}.dcm",1)
    print(df.head(3))

  patient_id abnormality type  assessment  \
0    P_00001             mass           4   
1    P_00001             mass           4   
2    P_00004             mass           4   

                          image file path  \
0   Mass-Training_P_00001_LEFT_CC/raw.dcm   
1  Mass-Training_P_00001_LEFT_MLO/raw.dcm   
2   Mass-Training_P_00004_LEFT_CC/raw.dcm   

                         cropped image file path  \
0   Mass-Training_P_00001_LEFT_CC_1/cropped1.dcm   
1  Mass-Training_P_00001_LEFT_MLO_1/cropped1.dcm   
2   Mass-Training_P_00004_LEFT_CC_1/cropped1.dcm   

                          ROI mask file path  
0   Mass-Training_P_00001_LEFT_CC_1/roi1.dcm  
1  Mass-Training_P_00001_LEFT_MLO_1/roi1.dcm  
2   Mass-Training_P_00004_LEFT_CC_1/roi1.dcm  
  patient_id abnormality type  assessment                     image file path  \
0    P_00016             mass           5   Mass-Test_P_00016_LEFT_CC/raw.dcm   
1    P_00016             mass           5  Mass-Test_P_00016_LEFT_MLO/raw.dcm  

C:\Users\yusuf\AppData\Local\Temp\ipykernel_14496\3707400491.py:8: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  df["image file path"] = df["image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +"raw.dcm",1)
C:\Users\yusuf\AppData\Local\Temp\ipykernel_14496\3707400491.py:9: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  df["cropped image file path"] = df["cropped image file path"].apply(lambda x: str(x)[:str(x).index("/")+1] +f"cropped{(str(x)[str(x).index('/')-1])}.dcm",1)
C:\Users\yusuf\AppData\Local\Temp\ipykernel_14496\3707400491.py:10: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``

In [114]:
# import shutil
# import os

# def move_file_to_parent_folder(file_path, i):
#     # Get the parent folder path
#     parent_folder = os.path.dirname(file_path)
    
#     # Get the grandparent folder path
#     grandparent_folder = os.path.dirname(parent_folder)
    
#     # Move the file to the grandparent folder
#     try:
#         shutil.move(file_path, os.path.dirname(grandparent_folder))
#     except Exception as e:
#         print(i, "   ",file_path)
#     return grandparent_folder

# # Example usage:

# for i in range(metadata_df["File Location"].shape[0]):
#     path = os.path.join(DATA_PATH, metadata_df["File Location"][i][2:])
#     grandparent_folder = ""
#     for dirpath, dirname, filenames in os.walk(path):
#         for f in filenames:
#             file_path = os.path.join(path,f)
#             grandparent_folder = move_file_to_parent_folder(file_path,i)
#     try:
#         shutil.rmtree(grandparent_folder)
#     except Exception as e:
#         pass

In [15]:
def find_subfolders(root_dir):
    subfolders = []
    for foldername, subfolders, filenames in os.walk(root_dir):
        if subfolders:
            subfolders.append(foldername)
    return subfolders

root_directory = DATA_PATH + "/CBIS-DDSM"

folders_with_subfolders = find_subfolders(root_directory)

print("Folders with subfolders:")
for folder in folders_with_subfolders:
    print(folder)

Folders with subfolders:


In [16]:
calc_test.head()

patient_id abnormality type  assessment  \
0    P_00038    calcification           4   
1    P_00038    calcification           4   
2    P_00038    calcification           2   
3    P_00038    calcification           2   
4    P_00038    calcification           2   

                       image file path  \
0    Calc-Test_P_00038_LEFT_CC/raw.dcm   
1   Calc-Test_P_00038_LEFT_MLO/raw.dcm   
2   Calc-Test_P_00038_RIGHT_CC/raw.dcm   
3   Calc-Test_P_00038_RIGHT_CC/raw.dcm   
4  Calc-Test_P_00038_RIGHT_MLO/raw.dcm   

                      cropped image file path  \
0    Calc-Test_P_00038_LEFT_CC_1/cropped1.dcm   
1   Calc-Test_P_00038_LEFT_MLO_1/cropped1.dcm   
2   Calc-Test_P_00038_RIGHT_CC_1/cropped1.dcm   
3   Calc-Test_P_00038_RIGHT_CC_2/cropped2.dcm   
4  Calc-Test_P_00038_RIGHT_MLO_1/cropped1.dcm   

                       ROI mask file path  
0    Calc-Test_P_00038_LEFT_CC_1/roi1.dcm  
1   Calc-Test_P_00038_LEFT_MLO_1/roi1.dcm  
2   Calc-Test_P_00038_RIGHT_CC_1/roi1.dcm  
3   Calc-Test_P_00038_RIGHT_CC_2/roi2.dcm  
4  Calc-Test_P_00038_RIGHT_MLO_1/roi1.dcm

In [17]:
for c in calc_test["cropped image file path"]:
    print(c)


Calc-Test_P_00038_LEFT_CC_1/cropped1.dcm
Calc-Test_P_00038_LEFT_MLO_1/cropped1.dcm
Calc-Test_P_00038_RIGHT_CC_1/cropped1.dcm
Calc-Test_P_00038_RIGHT_CC_2/cropped2.dcm
Calc-Test_P_00038_RIGHT_MLO_1/cropped1.dcm
Calc-Test_P_00038_RIGHT_MLO_2/cropped2.dcm
Calc-Test_P_00041_LEFT_CC_2/cropped2.dcm
Calc-Test_P_00041_LEFT_MLO_2/cropped2.dcm
Calc-Test_P_00077_LEFT_CC_1/cropped1.dcm
Calc-Test_P_00077_LEFT_MLO_1/cropped1.dcm
Calc-Test_P_00077_RIGHT_CC_1/cropped1.dcm
Calc-Test_P_00077_RIGHT_CC_2/cropped2.dcm
Calc-Test_P_00077_RIGHT_MLO_1/cropped1.dcm
Calc-Test_P_00077_RIGHT_MLO_2/cropped2.dcm
Calc-Test_P_00100_RIGHT_CC_1/cropped1.dcm
Calc-Test_P_00100_RIGHT_MLO_1/cropped1.dcm
Calc-Test_P_00127_RIGHT_CC_1/cropped1.dcm
Calc-Test_P_00127_RIGHT_MLO_1/cropped1.dcm
Calc-Test_P_00132_LEFT_MLO_1/cropped1.dcm
Calc-Test_P_00140_LEFT_CC_1/cropped1.dcm
Calc-Test_P_00140_LEFT_CC_2/cropped2.dcm
Calc-Test_P_00140_LEFT_MLO_1/cropped1.dcm
Calc-Test_P_00140_LEFT_MLO_2/cropped2.dcm
Calc-Test_P_00140_RIGHT_CC_1/crop

In [18]:
calc_test["cropped image file path"].iloc[0]

'Calc-Test_P_00038_LEFT_CC_1/cropped1.dcm'

In [193]:
# for df in [calc_test, calc_train, mass_test, mass_train]:
#     for i in range(df.shape[0]):
#         cropped_file = df["cropped image file path"].iloc[i]
#         cropped_label_text = cropped_file[:-7]
#         cropped_filename = cropped_file[-7:]
#         cropped_path = os.path.join(DATA_PATH, "CBIS-DDSM\\"+cropped_label_text)
        
#         old_file_path_cropped = os.path.join(cropped_path, cropped_filename)
#         new_file_path_cropped = os.path.join(cropped_path, "cropped"+cropped_label_text[-2]+".dcm")

#         df["cropped image file path"].iloc[i] = cropped_label_text + "cropped"+cropped_label_text[-2]+".dcm"

#         # Rename the file
#         try:
#             os.rename(old_file_path_cropped, new_file_path_cropped)
#         except(FileNotFoundError) as e:
#             pass
#         roi_file = df["ROI mask file path"].iloc[i]
#         roi_label_text = roi_file[:-7]
#         roi_filename = roi_file[-7:]
#         roi_path = os.path.join(DATA_PATH, "CBIS-DDSM\\"+roi_label_text)
        
#         old_file_path_roi = os.path.join(roi_path, roi_filename)
#         new_file_path_roi = os.path.join(roi_path, "roi"+roi_label_text[-2]+".dcm")

#         df["ROI mask file path"].iloc[i] = roi_label_text + "roi"+roi_label_text[-2]+".dcm"

#         # Rename the file
#         try:
#             os.rename(old_file_path_roi, new_file_path_roi)
#         except(FileNotFoundError) as e:
#             pass
#         raw_file = df["image file path"].iloc[i]
#         raw_label_text = raw_file[:-7]
#         raw_filename = raw_file[-7:]
#         raw_path = os.path.join(DATA_PATH, "CBIS-DDSM\\"+raw_label_text)
        
#         old_file_path_raw = os.path.join(raw_path, raw_filename)
#         new_file_path_raw = os.path.join(raw_path, "raw.dcm")
        
#         df["image file path"].iloc[i] = raw_label_text + "raw.dcm"

#         # Rename the file
#         try:
#             os.rename(old_file_path_raw, new_file_path_raw)
#         except(FileNotFoundError) as e:
#             pass

C:\Users\yusuf\AppData\Local\Temp\ipykernel_1228\980983734.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["cropped image file path"].iloc[i] = cropped_label_text + "cropped"+cropped_label_text[-2]+".dcm"
C:\Users\yusuf\AppData\Local\Temp\ipykernel_1228\980983734.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["ROI mask file path"].iloc[i] = roi_label_text + "roi"+roi_label_text[-2]+".dcm"
C:\Users\yusuf\AppData\Local\Temp\ipykernel_1228\980983734.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata

In [19]:
calc_test["ROI mask file path"].str.contains("1-").sum()

0

In [20]:
calc_test.head(6)

patient_id abnormality type  assessment  \
0    P_00038    calcification           4   
1    P_00038    calcification           4   
2    P_00038    calcification           2   
3    P_00038    calcification           2   
4    P_00038    calcification           2   
5    P_00038    calcification           2   

                       image file path  \
0    Calc-Test_P_00038_LEFT_CC/raw.dcm   
1   Calc-Test_P_00038_LEFT_MLO/raw.dcm   
2   Calc-Test_P_00038_RIGHT_CC/raw.dcm   
3   Calc-Test_P_00038_RIGHT_CC/raw.dcm   
4  Calc-Test_P_00038_RIGHT_MLO/raw.dcm   
5  Calc-Test_P_00038_RIGHT_MLO/raw.dcm   

                      cropped image file path  \
0    Calc-Test_P_00038_LEFT_CC_1/cropped1.dcm   
1   Calc-Test_P_00038_LEFT_MLO_1/cropped1.dcm   
2   Calc-Test_P_00038_RIGHT_CC_1/cropped1.dcm   
3   Calc-Test_P_00038_RIGHT_CC_2/cropped2.dcm   
4  Calc-Test_P_00038_RIGHT_MLO_1/cropped1.dcm   
5  Calc-Test_P_00038_RIGHT_MLO_2/cropped2.dcm   

                       ROI mask file path  
0    Calc-Test_P_00038_LEFT_CC_1/roi1.dcm  
1   Calc-Test_P_00038_LEFT_MLO_1/roi1.dcm  
2   Calc-Test_P_00038_RIGHT_CC_1/roi1.dcm  
3   Calc-Test_P_00038_RIGHT_CC_2/roi2.dcm  
4  Calc-Test_P_00038_RIGHT_MLO_1/roi1.dcm  
5  Calc-Test_P_00038_RIGHT_MLO_2/roi2.dcm

In [205]:
# Function to move files into a folder
# def move_files(source_dir, target_dir):
#     for filename in os.listdir(source_dir):
#         # Check if the file is not a directory
#         if os.path.isfile(os.path.join(source_dir, filename)):
#             # Move the file to the target directory
#             shutil.move(os.path.join(source_dir, filename), target_dir)

# # Function to group and move files
# def group_and_move(raw_dir, roi_dir, cropped_roi_dir, destination_dir):
#     for filename in os.listdir(raw_dir):
#         # Check if the file is not a directory
#         if os.path.isfile(os.path.join(raw_dir, filename)):
#             # Check if corresponding files exist in other directories
#             if os.path.exists(os.path.join(roi_dir, filename)) and \
#                os.path.exists(os.path.join(cropped_roi_dir, filename)):
#                 # Create a new folder for the image
#                 new_folder = os.path.join(destination_dir, filename.split('.')[0])
#                 os.makedirs(new_folder, exist_ok=True)
#                 # Move the files into the new folder
#                 move_files(roi_dir, new_folder)
#                 move_files(cropped_roi_dir, new_folder)

# for df in [calc_test, calc_train, mass_test, mass_train]:
#     for i in range(df.shape[0]):
#         raw_file = df["image file path"].iloc[i]
#         raw_label_text = raw_file[:-7]
#         raw_filename = raw_file[-7:]
#         raw_path = os.path.join(DATA_PATH, "CBIS-DDSM\\"+raw_label_text)
        
        
#         roi_file = df["ROI mask file path"].iloc[i]
#         roi_label_text = roi_file[:-7]
#         roi_filename = roi_file[-7:]
#         roi_path = os.path.join(DATA_PATH, "CBIS-DDSM\\"+roi_label_text)


In [1]:
calc_test.head(6)

NameError: name 'calc_test' is not defined

In [76]:
def find_roi_coordinates(pixel_array):
    # Pixel array'deki beyaz piksellerin konumlarını bul
    white_pixels = np.where(pixel_array == 255)

    # ROI'nin koordinatlarını hesapla
    x_min = np.min(white_pixels[1])
    x_max = np.max(white_pixels[1])
    y_min = np.min(white_pixels[0])
    y_max = np.max(white_pixels[0])

    # ROI'nin merkez koordinatlarını ve boyutlarını hesapla
    x_center = (x_min + x_max) / 2
    y_center = (y_min + y_max) / 2
    width = x_max - x_min
    height = y_max - y_min
    return x_center, y_center, width, height


# fig = plt.figure(figsize=(15, 30))


for df in [mass_train]:

    df["ROI x_center"] = np.zeros(df.shape[0])
    df["ROI y_center"] = np.zeros(df.shape[0])
    df["ROI width"] = np.zeros(df.shape[0])
    df["ROI height"] = np.zeros(df.shape[0])

    for i in range(df.shape[0]):
        roi_file = DATA_PATH + "CBIS-DDSM/" +df["ROI mask file path"].iloc[i]
        ds = pydicom.dcmread(roi_file)
        x_center, y_center, width, height = find_roi_coordinates(ds.pixel_array)
        # print("ROI Merkez Koordinatları (x, y):", x_center, y_center)
        # print("ROI Boyutları (Genişlik, Yükseklik):", width, height)

        df.iloc[i, 6] = x_center
        df.iloc[i,7] = y_center
        df.iloc[i,8] = width
        df.iloc[i,9] = height

        # fig.add_subplot(1, 2, i+1).set_title(str(x_center) + " "+ str(y_center) + " "+ str(width) + " "+ str(height))
        # plt.imshow(ds.pixel_array, plt.cm.gray)
        print(i)
# plt.show()

0
1
2
3
4
5
6
7


ValueError: zero-size array to reduction operation minimum which has no identity

In [155]:
for i in range(927,mass_train.shape[0]):
    roi_path = DATA_PATH + "CBIS-DDSM/" + mass_train["ROI mask file path"].iloc[i]
    cropped_path = DATA_PATH + "CBIS-DDSM/" + mass_train["cropped image file path"].iloc[i]

    c_size = os.path.getsize(cropped_path)
    try:
        r_size = os.path.getsize(roi_path)
    except:
        r_size = c_size -1
    
    if(r_size < c_size):

        roi_file = mass_train["ROI mask file path"].iloc[i]
        roi_label_text = roi_file[:-8]
        roi_filename = roi_file[-8:]
        
        cropped_file = mass_train["cropped image file path"].iloc[i]
        cropped_label_text = cropped_file[:-12]
        cropped_filename = cropped_file[-12:]

        if(r_size == c_size-1):
            os.rename(cropped_path, DATA_PATH + "CBIS-DDSM/" + cropped_label_text + roi_filename)
            os.rename(DATA_PATH + "CBIS-DDSM/" + roi_label_text + "temp.dcm", DATA_PATH + "CBIS-DDSM/" + roi_label_text + cropped_filename)
            continue

        os.rename(roi_path, DATA_PATH + "CBIS-DDSM/" + roi_label_text + "temp.dcm")
        
        os.rename(cropped_path, DATA_PATH + "CBIS-DDSM/" + cropped_label_text + roi_filename)

        os.rename(DATA_PATH + "CBIS-DDSM/" + roi_label_text + "temp.dcm", DATA_PATH + "CBIS-DDSM/" + roi_label_text + cropped_filename)

        
    print(i)

927


FileNotFoundError: [WinError 3] The system cannot find the path specified: '..\\data CBIS-DDSM\\CBIS-DDSM/Mass-Training_P_01326_LEFT_MLO_1/cropped1.dcm'

In [54]:
# fig = plt.figure(figsize=(15, 30))

# plt.imshow(pydicom.dcmread("D:/Teknofest/Sağlıkta yapay zeka/data CBIS-DDSM/CBIS-DDSM/Mass-Test_P_00145_LEFT_MLO_1/cropped1.dcm").pixel_array, plt.cm.gray)